In [1]:
import petl as etl
import pandas as pd

In [75]:
# Import CSV through PETL and create table.

df = etl.fromcsv('resources/rush.csv')
injury_df = etl.fromcsv('resources/injuries.csv')
etl.lookall(injury_df)

+--------+-----------+-------+------+--------------+----------+------------------------------+---------------+--------------------+----------------------------------------+----------------------------------------+----------------+----------------------------------------+----------------------------------+-------------------------------------+-----------------------------+
| season | game_type | team  | week | gsis_id      | position | full_name                    | first_name    | last_name          | report_primary_injury                  | report_secondary_injury                | report_status  | practice_primary_injury                | practice_secondary_injury        | practice_status                     | date_modified               |
+========+===========+=======+======+==============+==========+==============================+===============+====================+========================================+========================================+================+====================

In [76]:
# Create new table for rushing yards based on rows we want to use.
rushing_df = etl.cut(df, 'player', 'pos', 'yds', 'td')

# Convert string values to floats on yards and touchdown columns.
convert_columns = {
    'yds': float,
    'td': float
}
convert_rushing = etl.convert(rushing_df, convert_columns)
sorted_rushing = etl.sort(convert_rushing, key='yds', reverse=True)

etl.lookall(sorted_rushing)

+----------------------------+------+--------+------+
| player                     | pos  | yds    | td   |
+============================+======+========+======+
| 'Josh Jacobs'              | 'RB' | 1653.0 | 12.0 |
+----------------------------+------+--------+------+
| 'Derrick Henry'            | 'RB' | 1538.0 | 13.0 |
+----------------------------+------+--------+------+
| 'Nick Chubb'               | 'RB' | 1525.0 | 12.0 |
+----------------------------+------+--------+------+
| 'Saquon Barkley'           | 'RB' | 1312.0 | 10.0 |
+----------------------------+------+--------+------+
| 'Miles Sanders'            | 'RB' | 1269.0 | 11.0 |
+----------------------------+------+--------+------+
| 'Dalvin Cook'              | 'RB' | 1173.0 |  8.0 |
+----------------------------+------+--------+------+
| 'Justin Fields'            | 'QB' | 1143.0 |  8.0 |
+----------------------------+------+--------+------+
| 'Christian McCaffrey'      | 'RB' | 1139.0 |  8.0 |
+---------------------------

In [77]:
# Rename column to player to correctly merge tables.
injury_df = etl.rename(injury_df, {'full_name': 'player'})

# Transform injury csv to have only the columns we want.
injury_cleaned = etl.cut(injury_df, 'player', 'position', 'report_primary_injury', 'report_secondary_injury', 'report_status', 'practice_primary_injury', 'practice_secondary_injury')
etl.lookall(injury_cleaned)

+------------------------------+----------+----------------------------------------+----------------------------------------+----------------+----------------------------------------+----------------------------------+
| player                       | position | report_primary_injury                  | report_secondary_injury                | report_status  | practice_primary_injury                | practice_secondary_injury        |
+==============================+==========+========================================+========================================+================+========================================+==================================+
| 'Rodney Hudson'              | 'C'      | ''                                     | ''                                     | ''             | 'Not injury related - resting player'  | ''                               |
+------------------------------+----------+----------------------------------------+----------------------------------------

In [67]:
# Check to make sure both the rushing and injury tables can be joined successfully.
merged = etl.join(sorted_rushing, injury_cleaned, key='player')
etl.lookall(merged)

+----------------------------+------+--------+------+----------+----------------------------------------+----------------------------------------+----------------+----------------------------------------+----------------------------------+
| player                     | pos  | yds    | td   | position | report_primary_injury                  | report_secondary_injury                | report_status  | practice_primary_injury                | practice_secondary_injury        |
+============================+======+========+======+==========+========================================+========================================+================+========================================+==================================+
| 'Aaron Jones'              | 'RB' | 1121.0 |  2.0 | 'RB'     | ''                                     | ''                                     | ''             | 'Ankle'                                | ''                               |
+----------------------------+------+---

In [125]:
# Export both tables to csv file.
etl.tocsv(sorted_rushing, 'output_data/rushing_cleaned.csv')
etl.tocsv(injury_cleaned, 'output_data/injury_cleaned.csv')

In [2]:
# Import the partially cleaned injury csv using pandas. 
injury_new_df = pd.read_csv('output_data/injury_cleaned.csv')
injury_new_df


player position report_primary_injury report_secondary_injury  \
0      Rodney Hudson        C                   NaN                     NaN   
1       Aaron Brewer       LS                   NaN                     NaN   
2      Markus Golden       LB                   NaN                     NaN   
3     Ezekiel Turner       LB                   NaN                     NaN   
4      Jonathan Ward       RB                   NaN                     NaN   
...              ...      ...                   ...                     ...   
5677     Jason Kelce        C                   NaN                     NaN   
5678   Isaac Seumalo        G                   NaN                     NaN   
5679     Darius Slay       CB                   NaN                     NaN   
5680      Josh Sweat       DE                   NaN                     NaN   
5681   Britain Covey       WR             Hamstring                     NaN   

     report_status              practice_primary_injury  \
0              NaN  Not injury related - resting player   
1              NaN                                Ankle   
2              NaN                                  Toe   
3              NaN                             Shoulder   
4              NaN                             Shoulder   
...            ...                                  ...   
5677           NaN  Not injury related - resting player   
5678           NaN  Not injury related - resting player   
5679           NaN  Not injury related - resting player   
5680           NaN  Not injury related - resting player   
5681  Questionable                            Hamstring   

     practice_secondary_injury  
0                          NaN  
1                          NaN  
2                          NaN  
3                          NaN  
4                          NaN  
...                        ...  
5677                       NaN  
5678                       NaN  
5679                       NaN  
5680                       NaN  
5681                       NaN  

[5682 rows x 7 columns]

In [4]:
# Since PETL was having issues with object types and dropping NaN values 
# we imported pandas to check for null values and drop them from the DF.
check_columns = [
    'report_primary_injury', 
    'report_secondary_injury', 
    'report_status', 
    'practice_primary_injury', 
    'practice_secondary_injury'
]

injury_new_df.dropna(subset=check_columns, inplace=True)


(197, 7)

In [5]:
# Checking injury DF for unique values
unique_players = injury_new_df['player'].unique()
counts = injury_new_df['player'].value_counts()
print(unique_players)
print(counts)

['Marcus Peters' 'Mike Woods' 'Randy Gregory' 'K.J. Hamler'
 'Elgton Jenkins' 'Damien Lewis' 'Christopher Hubbard' 'Frank Ragnow'
 'Jerry Jeudy' 'Josey Jewell' 'Cedrick Wilson' 'Jameis Winston'
 'John Franklin-Myers' 'Shelby Harris' 'J.J. Watt' 'Ronnie Stanley'
 'Dawson Knox' 'David Montgomery' 'Myles Garrett' "D'Andre Swift"
 'Pharaoh Brown' 'Corey Linsley' 'Xavien Howard' 'Tua Tagovailoa'
 'Breshad Perriman' 'Russell Gage' 'Julio Jones' 'Chris Godwin'
 'Quinton Bohanna' 'Shaquille Leonard' 'JuJu Smith-Schuster'
 'Keion Crossen' 'Cameron Sutton' 'Marquise Goodwin' 'Arik Armstead'
 'Nate Davis' 'Melvin Gordon' 'Teddy Bridgewater' 'Gabe Jackson'
 'Justin Houston' 'James Pierre' 'Divine Deablo' 'Tyler Lockett'
 'Mark Andrews' 'Preston Smith' 'Brandin Cooks' 'Dennis Kelly'
 'Joe Fortson' 'Austin Jackson' 'Terron Armstead' 'Akiem Hicks'
 'Matt Prater' 'Tremaine Edmunds' 'Eric Stokes' 'Jerick McKinnon'
 'Denzel Perryman' 'Hunter Long' 'Jason Verrett' 'Samson Ebukam'
 'Gus Edwards' 'Juston B

In [6]:
# Checking for duplicates
duplicates = injury_new_df[injury_new_df.duplicated()]
injury_new_df.duplicated().sum()

32

In [7]:
# Dropping duplicates 
injury_new_df.drop_duplicates(inplace=True)
injury_new_df.duplicated().sum()

0

In [8]:
# Exporting fully cleaned injury DF to CSV.
injury_new_df.to_csv('output_data/injury_cleaned.csv', index=False)


next things to do 
1. figure out count for which position has the most injuries
2. figure out inputs